In [81]:
import numpy as np
import math
from copy import deepcopy
import sklearn.datasets
from sklearn.svm import SVC

In [64]:
X,y = sklearn.datasets.make_hastie_10_2()
X_train = X[0:8000,:]
y_train = y[0:8000]
X_test = X[8000:,:]
y_test = y[8000:]

In [72]:
class SVC_:
    def __init__(self, kernel="rbf", degree="3"):
        self.svc = SVC(kernel=kernel, degree=degree)

    def fit(self, X, y, sample_weight=None):
        if sample_weight is not None:
            sample_weight = sample_weight * len(X)

        self.svc.fit(X,y,sample_weight=sample_weight)
        return self

    def predict(self, X):
        return self.svc.predict(X)

# Exercise 1

1. Implement the AdaBoost ensemble algorithm by completing the following code:

In [226]:
class AdaBoost:
    def __init__(self, weakModel, T):
        self.model = weakModel
        self.models = []
        self.T = T
        self.a = []

    def fit(self, X, y):
        w = [1 / len(X) for x in X]
        for t in range(self.T):
            model = deepcopy(self.model)
            model.fit(X, y, sample_weight = w)
            predictions = model.predict(X)
            self.models.append(model)
            e = sum([w[i] if predictions[i] != y[i] else 0 for i in range(len(y))])
            if t%10 == 0:
                print("Weighted Error:", e)
            a = np.log((1 - e) / e) / 2
            self.a.append(a)
            w = [w[i] * np.exp(-a * y[i] * predictions[i]) for i in range(len(w))]
            w /= sum(w)
        return self

    def predict(self, X):
        return np.sign(sum([self.a[t] * self.models[t].predict(X) for t in range(self.T)]))

In the implementation you are free to assume:
- that the problem is a binary classification problem with labels in $\{-1, +1\}$.
- that the weakModel can fit a weighted sample set by means of the call `weakModel.fit(X,y,sample_weight=w)` where `w` is a vector of length $|y|$.

2. Test your implementation on the dataset loaded above and using an SVC with a polynomial kernel. 

In [227]:
weakModel = SVC(kernel="poly", degree=3)
adaboost = AdaBoost(weakModel, 10)
adaboost.fit(X_train, y_train)
y_test_ = adaboost.predict(X_test)

C:\Users\galat\.conda\envs\aaut\lib\site-packages\sklearn\svm\base.py:193: FutureWarning: The default value of gamma will change from 'auto' to 'scale' in version 0.22 to account better for unscaled features. Set gamma explicitly to 'auto' or 'scale' to avoid this warning.
  "avoid this warning.", FutureWarning)


Weighted Error: 0.49512499999995935


C:\Users\galat\.conda\envs\aaut\lib\site-packages\sklearn\svm\base.py:193: FutureWarning: The default value of gamma will change from 'auto' to 'scale' in version 0.22 to account better for unscaled features. Set gamma explicitly to 'auto' or 'scale' to avoid this warning.
  "avoid this warning.", FutureWarning)
C:\Users\galat\.conda\envs\aaut\lib\site-packages\sklearn\svm\base.py:193: FutureWarning: The default value of gamma will change from 'auto' to 'scale' in version 0.22 to account better for unscaled features. Set gamma explicitly to 'auto' or 'scale' to avoid this warning.
  "avoid this warning.", FutureWarning)
C:\Users\galat\.conda\envs\aaut\lib\site-packages\sklearn\svm\base.py:193: FutureWarning: The default value of gamma will change from 'auto' to 'scale' in version 0.22 to account better for unscaled features. Set gamma explicitly to 'auto' or 'scale' to avoid this warning.
  "avoid this warning.", FutureWarning)
C:\Users\galat\.conda\envs\aaut\lib\site-packages\sklearn\

In [123]:
print(0.5 - (y_test.dot(y_test_)) / (2 * len(y_test)))

0.49425


3. evaluate the AdaBoost performances as usual by calculating the classification error and compare it with the classification error of the weak model.

**Note 1**:  
since the labels are bound to be in ${+1, -1}$, the classification error (i.e., the number of incorrectly classified examples over the total number of examples) can be easily computed as:
$$
   error(y,y') = \frac{N - y \cdot y'}{2N} = \frac{1}{2} - \frac{y \cdot y'}{2N},
$$
where $N$ is the total number of examples. The formula can be derived noticing that $y \cdot y'$ calculates the number $N_c$ of examples correctly classified  minus the number $N_{\bar c}$ of examples incorrectly classified. We have then $y \cdot y' = N_c - N_{\bar c}$ and by noticing that $N = N_c + N_{\bar c}$:
$$
   N - y \cdot y' = N_c + N_{\bar c} - N_c + N_{\bar c} = 2 N_{\bar c} \Rightarrow \frac{N - y \cdot y'}{2 N} = \frac{N_{\bar c}}{N}
$$

**Note 2**:
do not forget to deepcopy your base model before fitting it to the new data

**Note 3**:
The SVC model allows specifying weights, but it *does not* work well when weights are normalized (it works well when the weights are larger). The following class takes normalized weights and denormalize them before passing them to the SVC classifier:

```python
    class SVC_:
        def __init__(self, kernel="rbf", degree="3"):
            self.svc = SVC(kernel=kernel, degree=degree)

        def fit(self, X,y,sample_weight=None):
            if sample_weight is not None:
                sample_weight = sample_weight * len(X)

            self.svc.fit(X,y,sample_weight=sample_weight)
            return self

        def predict(self, X):
            return self.svc.predict(X)
```

# Exercise 2

1. Write a weak learner to be used with the AdaBoost algorithm you just wrote. The weak learner that you will implement is the most inaccurate weak learner possible: it basically works by extracting a linear model at random and trying to use that model to classify the examples. Being extracted at random the models it generates do not guarantee that the weighted error $\epsilon_t$ is smaller than $0.5$. The algorithm solves this problem by flipping the decisions whenever it finds out that $\epsilon_t > 0.5$ (i.e., if the weighted error is larger than $0.5$ it reverses the sign of all the weights so that the decision surface stays the same, but the regions where it predicts $+1$ and $-1$ are reversed).

    It shall work as follows:

    - it creates a random linear model by generating the needed weight vector $\mathbf{w}$ at random (**note**: these are the weights of the linear model, they are *NOT* related in any way to the weights of the examples); each weight shall be sampled from U(-1,1);
    - it evaluates the weighted loss $\epsilon_t$ on the given dataset and flip the linear model if $\epsilon_t > 0.5$;
    - at prediction time it predicts +1 if $\mathbf{x} \cdot \mathbf{w} > 0$; it predicts -1 otherwise.

In [222]:
class RandomLinearModel:
    def loss(self, y, y_, sample_weight):
        return sum([sample_weight[i] if y[i] != y_[i] else 0 for i in range(len(y))])
        
    def fit(self,X,y,sample_weight=[]):
        self.w = np.random.rand(len(X[0])) * 2 - 1
        if len(sample_weight) == 0:
            sample_weight = [1 / len(X) for x in X]
        if self.loss(y, self.predict(X), sample_weight) > 0.5:
            self.w *= -1
        return self
        
    def predict(self,X):
        return np.sign(X.dot(self.w))

In [228]:
rs = RandomLinearModel()
rs.fit(X_train, y_train)
predictions = rs.predict(X_test)
print(0.5 - y_test.dot(predictions)/(2 * len(y_test)))

0.487


2. Learn an AdaBoost model using the RandomLinearModel weak learner printing every $K$ iterations the weighted error and the current error of the ensemble (you are free to choose $K$ so to make your output just frequent enough to let you know what is happening but without flooding the console with messages). Evaluate the training and test error of the final ensemble model.

In [229]:
rs = RandomLinearModel()
a = AdaBoost(rs,100)
a.fit(X_train,y_train)

y_train_ = a.predict(X_train)
y_test_ = a.predict(X_test)

Weighted Error: 0.49524999999995933
Weighted Error: 0.4948541341954795
Weighted Error: 0.49729398392530305
Weighted Error: 0.49980867302257964
Weighted Error: 0.49683487146024025
Weighted Error: 0.49790489175815233
Weighted Error: 0.4940625587347454
Weighted Error: 0.4950371378338745
Weighted Error: 0.4909255291281916
Weighted Error: 0.4960331784908466


In [232]:
print("Training Error:", 0.5 - y_train.dot(y_train_)/(2 * len(y_train)))
print("Test Error:", 0.5 - y_test.dot(y_test_)/(2 * len(y_test)))

Training Error: 0.462125
Test Error: 0.49375


3. Write few paragraphs about what you think about the experiment and about the results you obtained.